In [1]:
import ast
import numpy as np
import random
import torch

from datasets import load_dataset
from huggingface_hub import hf_hub_download
from torch.utils.data import DataLoader
from transformers import AutoTokenizer
from tqdm import tqdm

from model.scibert import SciBertClassificationModel

/home/ppak/GitHub/LLM-Enabled-Process-Map/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Set the seed for Python's random module
random.seed(42)

# Set the seed for NumPy
np.random.seed(42)

# Set the seed for PyTorch
torch.manual_seed(42)

# Ensure reproducibility on GPUs
if torch.cuda.is_available():
    torch.cuda.manual_seed(42)
    torch.cuda.manual_seed_all(42)  # For multi-GPU setups

# Optional: Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

In [3]:
# Initialize the model
model = SciBertClassificationModel("ppak10/defect-classification-scibert-baseline-05-epochs")

# model.classifier.load_state_dict(torch.load(classification_head_path))
model.eval()  # Set the model to evaluation mode

SciBertClassificationModel(
  (base_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(31090, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps

In [4]:
# Load dataset
dataset = load_dataset("ppak10/melt-pool-classification", cache_dir="./.cache")
train_dataset = dataset["train_baseline"]
test_dataset = dataset["test_baseline"]
validation_dataset = dataset["validation_baseline"]

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained("ppak10/defect-classification-scibert-baseline-05-epochs")

# Preprocessing function
def preprocess_function(examples):
    examples["label"] = [ast.literal_eval(label) for label in examples["label"]]
    examples["label"] = [np.array(label, dtype=np.float32) for label in examples["label"]]
    return tokenizer(
        examples["text"], truncation=True, padding="max_length", max_length=256
    )

train_dataset_tokenized = train_dataset.map(preprocess_function, batched=True, num_proc=64)
test_dataset_tokenized = test_dataset.map(preprocess_function, batched=True, num_proc=32)
validation_dataset_tokenized = validation_dataset.map(preprocess_function, batched=True, num_proc=32)

Generating train split: 41311472 examples [00:36, 1125978.62 examples/s]
Generating test split: 1739424 examples [00:01, 1126572.80 examples/s]
Generating validation split: 797225 examples [00:00, 1612244.91 examples/s]
Generating train_baseline split: 543572 examples [00:00, 1922772.39 examples/s]
Generating test_baseline split: 108714 examples [00:00, 1808065.15 examples/s]
Generating validation_baseline split: 72475 examples [00:00, 2011155.84 examples/s]
Generating train_prompt split: 40767900 examples [00:34, 1185073.83 examples/s]
Generating test_prompt split: 1630710 examples [00:01, 1136271.75 examples/s]
Generating validation_prompt split: 724750 examples [00:00, 1768766.65 examples/s]
Map (num_proc=32): 100%|██████████| 72475/72475 [00:01<00:00, 45154.53 examples/s]


# With Pretrained Weights

In [5]:
classification_head_path = hf_hub_download(
    repo_id="ppak10/defect-classification-scibert-baseline-05-epochs",
    repo_type="model",
    filename="classification_head.pt"
)
model.classifier.load_state_dict(torch.load(classification_head_path))
model.eval()  # Set the model to evaluation mode

/tmp/ipykernel_2733400/1395191505.py:6: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.classifier.load_state_dict(torch.load(classification_head_path))


SciBertClassificationModel(
  (base_model): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(31090, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps

In [6]:
# Ensure the model is on the GPU
device = torch.device("cuda:1" if torch.cuda.is_available() else "cpu")
model = model.to(device)

# Define the batch size
batch_size = 512

# Create a DataLoader for the validation dataset
validation_loader = DataLoader(validation_dataset_tokenized, batch_size=batch_size, shuffle=False)

def label_to_classifications_batch(labels):
    classifications = ["Desirable", "Keyhole", "Lack of Fusion", "Balling"]
    
    results = []
    for label in labels:  # Iterate over each label in the batch
        result = [classifications[index] for index, encoding in enumerate(label) if encoding == 1]
        results.append(result)
    return results

accuracy_total = 0

# Process the validation dataset in batches
for batch in tqdm(validation_loader):
    texts = batch["text"]
    labels = np.array(batch["label"]).T

    # Move labels to GPU
    # print(np.array(labels))
    labels = torch.tensor(labels).to(device)

    # Tokenize input for the entire batch and move to GPU
    inputs = tokenizer(list(texts), return_tensors="pt", truncation=True, padding="max_length", max_length=256)
    inputs_kwargs = {}

    for key, value in inputs.items():
        if key not in ["token_type_ids"]:
            inputs_kwargs[key] = value.to(device)

    # print(inputs_kwargs)
    # inputs = {key: value.to(device) for key, value in inputs.items()}

    # Perform inference
    outputs = model(**inputs_kwargs)

    # Extract logits and apply sigmoid activation for multi-label classification
    logits = outputs["logits"]
    probs = torch.sigmoid(logits)

    # Convert probabilities to one-hot encoded labels
    preds = (probs > 0.5).int()

    # Compute accuracy for the batch
    accuracy_per_label = (preds == labels).float().mean(dim=1)  # Mean per sample
    accuracy_batch_mean = accuracy_per_label.mean().item()  # Mean for the batch

    accuracy_total += accuracy_batch_mean * len(labels)  # Weighted addition for overall accuracy

# Calculate overall accuracy
overall_accuracy = accuracy_total / len(validation_dataset_tokenized)

100%|██████████| 142/142 [08:58<00:00,  3.79s/it]


In [7]:
print(f"Overall Accuracy: {overall_accuracy}")

Overall Accuracy: 0.8829734390404521
